In [1]:
import pandas as pd
import numpy as np

from myclass.CleanMergeDataset import Clean_Merge_Dataset
from myclass.BonferroniTtest import Bonferroni_Ttest

In [2]:
data_normal = pd.read_pickle('./data-ready/RNA_dataframe_normal').replace('/', '\\')
data_tumor = pd.read_pickle('./data-ready/RNA_dataframe').replace('/', '\\')
dataset_RNA, y_RNA, cases_id_RNA = Clean_Merge_Dataset(name='RNA').transform(data_normal, data_tumor)
df_RNA = pd.concat([dataset_RNA, cases_id_RNA], axis=1)

Data_normal: (305, 60486)
Data_tumor: (1071, 60486)
All data: (1376, 60486)
{'TCGA-LUSC', 'TCGA-LUAD'}
Features completly 0 values 2227 removed
Features completely Nan 0 removed
Final dataset shape (959, 58258)


In [3]:
data_normal = pd.read_pickle('./data-ready/miRNA_dataframe_normal').replace('/', '\\')
data_tumor = pd.read_pickle('./data-ready/miRNA_dataframe').replace('/', '\\')
dataset_miRNA, y_miRNA, cases_id_miRNA= Clean_Merge_Dataset(name='miRNA').transform(data_normal, data_tumor)
df_miRNA = pd.concat([dataset_miRNA, cases_id_miRNA], axis=1)

Data_normal: (136, 1884)
Data_tumor: (623, 1884)
All data: (759, 1884)
{'TCGA-LUSC', 'TCGA-LUAD'}
Features completly 0 values 287 removed
Features completely Nan 0 removed
Final dataset shape (558, 1596)


In [4]:
data_normal = pd.read_pickle('./data-ready/illumina-27-450-normal').replace('/', '\\')
data_tumor = pd.read_pickle('./data-ready/illumina450-27-tumor').replace('/', '\\')
dataset_illumina, y_illumina, cases_id_illumina= Clean_Merge_Dataset(name='illumina').transform(data_normal, data_tumor)
df_illumina = pd.concat([dataset_illumina, cases_id_illumina], axis=1)

Data_normal: (125, 25981)
Data_tumor: (1082, 25981)
All data: (1207, 25981)
{'TCGA-LUSC', 'TCGA-LUAD'}
Features completly 0 values 0 removed
Features completely Nan 2597 removed
Final dataset shape (1206, 19697)


In [5]:
dataset_RNA = Bonferroni_Ttest(label_case_id_into_X=True, alpha=0.05).fit_transform(pd.concat([df_RNA, y_RNA], axis=1), y_RNA)

Final dataset shape: (959, 12963)


In [6]:
dataset_miRNA = Bonferroni_Ttest(label_case_id_into_X=True, alpha=0.05).fit_transform(pd.concat([df_miRNA, y_miRNA], axis=1), y_miRNA)

Final dataset shape: (558, 235)


In [7]:
dataset_illumina = Bonferroni_Ttest(label_case_id_into_X=True, alpha=0.05).fit_transform(pd.concat([df_illumina, y_illumina], axis=1), y_illumina)

Final dataset shape: (1206, 15698)


In [8]:
cases_id = set(dataset_illumina['case_id']) & set(dataset_miRNA['case_id']) & set(dataset_RNA['case_id'])
df_final_illumina = dataset_illumina.loc[dataset_illumina['case_id'].isin(cases_id)]
df_final_rna = dataset_RNA.loc[dataset_RNA['case_id'].isin(cases_id)]
df_final_mirna = dataset_miRNA.loc[dataset_miRNA['case_id'].isin(cases_id)]

In [9]:
print(df_final_illumina.shape)
print(df_final_rna.shape)
print(df_final_mirna.shape)

(493, 15700)
(508, 12965)
(473, 237)


In [10]:
print(len(cases_id))

449


In [11]:
import plotly.express as px
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot


correlation_matrix = df_final_rna.drop(['label', 'case_id'], axis=1).T.corr()

trace = go.Heatmap(z=correlation_matrix.values.tolist(),
                              x=df_final_rna['case_id'],
                              y= df_final_rna['case_id'])
data = [trace]
layout=go.Layout(title="Correlation matrix")
fig_heatmap = go.Figure(data=data, layout=layout)
iplot(fig_heatmap)